# 1.2 Import

One "Swiss knife" tool (or library) for each format:
- XML: `BeautifoulSoup`
- JSON: `jq`
- CSV: `csvkit`

<img src='https://cdn-images-1.medium.com/max/1600/1*Emm10TxVEOvWqwF9oPJb1w.jpeg' width='300px'>

## XML

### `BeautifulSoup`

There are several Python libraries to parse XML but `BeautifulSoup` is somehow the swiss knife of XML parsing.

It can parse HTML, XML, as well as ill-formed or broken XML documents (very useful for legacy XML or even SGML data).

In [4]:
import os
import bs4
from bs4 import BeautifulSoup

In [5]:
data_folder = '../data/altoxml/'

In [6]:
# let's get the path of XML files
# we filter only files with XML extension
# it can be useful to ignore e.g. `.DS_Store` files (under MacOS)

xml_files = [
    os.path.join(data_folder, file)
    for file in os.listdir(data_folder)
    if ".xml" in file
]

In [7]:
xml_files

['../data/altoxml/27971740_1890-04-01_38_077_0_003.xml',
 '../data/altoxml/27971740_1890-04-01_38_077_0_002.xml',
 '../data/altoxml/27971740_1890-04-01_38_077_0_001.xml',
 '../data/altoxml/27971740_1890-04-01_38_077_0_004.xml']

In [8]:
# prefixing a code cell's content with `!`
# tells jupyter to execute it as a bash shell command
# Here we use the command `head` to peek at the first 100 lines
# of our XML file.

!head -n 50 ../data/altoxml/27971740_1890-04-01_38_077_0_001.xml

﻿<?xml version="1.0" encoding="UTF-8" standalone="yes" ?>
<alto xmlns="http://www.loc.gov/standards/alto/ns-v2#" xmlns:xlink="http://www.w3.org/1999/xlink" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://www.loc.gov/standards/alto/ns-v2# http://www.loc.gov/standards/alto/alto-v2.0.xsd">
    <Description>
        <MeasurementUnit>pixel</MeasurementUnit>
        <OCRProcessing ID="IdOcr">
            <ocrProcessingStep>
                <processingDateTime>2014-10-22</processingDateTime>
                <processingSoftware>
                    <softwareCreator>ABBYY</softwareCreator>
                    <softwareName>ABBYY FineReader Engine</softwareName>
                    <softwareVersion>11</softwareVersion>
                </processingSoftware>
            </ocrProcessingStep>
        </OCRProcessing>
    </Description>
    <Styles>
        <TextStyle ID="font0" FONTFAMILY="Times New Roman" FONTSIZE="7" />
        <TextStyle ID="font1" FONTFAMILY="Tim

In [9]:
with open(xml_files[0], 'r') as inpfile:
    xml_doc = BeautifulSoup(inpfile)

In [10]:
xml_doc

<html><body><p>﻿<?xml version="1.0" encoding="UTF-8" standalone="yes" ?>
<alto xmlns="http://www.loc.gov/standards/alto/ns-v2#" xmlns:xlink="http://www.w3.org/1999/xlink" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemalocation="http://www.loc.gov/standards/alto/ns-v2# http://www.loc.gov/standards/alto/alto-v2.0.xsd">
<description>
<measurementunit>pixel</measurementunit>
<ocrprocessing id="IdOcr">
<ocrprocessingstep>
<processingdatetime>2014-10-22</processingdatetime>
<processingsoftware>
<softwarecreator>ABBYY</softwarecreator>
<softwarename>ABBYY FineReader Engine</softwarename>
<softwareversion>11</softwareversion>
</processingsoftware>
</ocrprocessingstep>
</ocrprocessing>
</description>
<styles>
<textstyle fontfamily="Courier New" fontsize="9" id="font0"></textstyle>
<textstyle fontfamily="Times New Roman" fontsize="5" id="font1"></textstyle>
<textstyle fontfamily="Times New Roman" fontsize="8" id="font2"></textstyle>
<textstyle fontfamily="Times New Roman" fontsi

### Finding elements

Finding the `<textblock>` element with `@id` = `Page1_Block2`:

In [11]:
xml_doc.find_all?

In [15]:
target_element = xml_doc.find_all(
    'textblock',
    attrs={'id': 'Page1_Block1'}
)

In [17]:
# by definition, there should exist excatly one element
# with a given ID within the same document
assert len(target_element) == 1

The same search logic applies to *any* XML attribute. 

Here we search for all `<composedblock>` with `@type` = `container`:

In [18]:
composed_blocks = xml_doc.find_all(
    'composedblock',
    {'type': 'container'}
)

Finding all XML elements with a given name:

In [20]:
textline_elements = xml_doc.find_all('textline')

In [26]:
x = textline_elements[0].get('vpos')
y = textline_elements[0].get('hpos')
w = textline_elements[0].get('width')
h = textline_elements[0].get('height')

In [27]:
print(
    f'The coordinates of the first line are : {x} (x), {y} (y), {h} (height), {w} (width)'
)

The coordinates of the first line are : 466 (x), 242 (y), 86 (height), 611 (width)


### Navigating the XML tree

In [21]:
el = xml_doc.find('styles')

In [27]:
for child in el.children:
    print(type(child), child.name)

<class 'bs4.element.NavigableString'> None
<class 'bs4.element.Tag'> textstyle
<class 'bs4.element.NavigableString'> None
<class 'bs4.element.Tag'> textstyle
<class 'bs4.element.NavigableString'> None
<class 'bs4.element.Tag'> textstyle
<class 'bs4.element.NavigableString'> None
<class 'bs4.element.Tag'> textstyle
<class 'bs4.element.NavigableString'> None
<class 'bs4.element.Tag'> textstyle
<class 'bs4.element.NavigableString'> None
<class 'bs4.element.Tag'> textstyle
<class 'bs4.element.NavigableString'> None
<class 'bs4.element.Tag'> textstyle
<class 'bs4.element.NavigableString'> None
<class 'bs4.element.Tag'> textstyle
<class 'bs4.element.NavigableString'> None
<class 'bs4.element.Tag'> textstyle
<class 'bs4.element.NavigableString'> None
<class 'bs4.element.Tag'> textstyle
<class 'bs4.element.NavigableString'> None


In [29]:
parent = el.parent

In [30]:
el.previousSibling

'\n'

In [31]:
el.nextSibling

'\n'

### [Excercise] From XML to dictionary

Let's now try to put all these things together to solve a real problem that you have already encountered, i.e. **turning a bunch of XML files into processable data**. Why this can be useful?

(This exercise will take around 20-30 minutes to complete).

In [32]:
import pandas as pd

In [3]:
def parse_alto(filepath):
    """
    Convert each file to a dictionary with the
    following keys: fulltext (list of lines), wordcount, filename.
    """
    parsed_data = {}
    
    # add here your solution
    # you'll need to parse the xml elements
    # containing the information you are interested in
    
    # HINT: you may want to split the parsing of individual
    # XML elements into dedicated functions that get called from
    # `parse_alto()`
    
    return parsed_data

In [34]:
# once your function is in place, you should be
# able to execute this cell, which applies your function
# to all Alto files.

data = [
    parse_alto(xml_file)
    for xml_file in xml_files
]

df = pd.DataFrame(data)

In [35]:
df.head()

Empty DataFrame
Columns: []
Index: [0, 1, 2, 3]

## JSON

`jq` is an extremely powerful utility to read/process/transform JSON files.

Why bother? There is **a lot** you can do with `jq` on any JSON file without writing lines of Python but with a single command line.

**NB**: `jq` is installed at the level of operative system and works as a command line tool. In this notebook, we use the `!` at the beginning of each cell we want Jupyter to process and execute as a bash command (instead of a Python statement).  

In [114]:
!jq --help

jq - commandline JSON processor [version 1.5rc2-43-g6fa1300]
Usage: jq [options] <jq filter> [file...]

	jq is a tool for processing JSON inputs, applying the
	given filter to its JSON text inputs and producing the
	filter's results as JSON on standard output.
	The simplest filter is ., which is the identity filter,
	copying jq's input to its output unmodified (except for
	formatting).
	For more advanced filters see the jq(1) manpage ("man jq")
	and/or https://stedolan.github.io/jq

	Some of the options include:
	 -c		compact instead of pretty-printed output;
	 -n		use `null` as the single input value;
	 -e		set the exit status code based on the output;
	 -s		read (slurp) all inputs into an array; apply filter to it;
	 -r		output raw strings, not JSON texts;
	 -R		read raw strings, not JSON texts;
	 -C		colorize JSON;
	 -M		monochrome (don't colorize JSON);
	 -S		sort keys of objects on output;
	 --tab	use tabs for indentation;
	 --arg a v	set variable $a to value <v>;
	 --argjson a v	

<img src=''> What happens if you remove the `!` ? Can you tell what's happening ?

In [38]:
json_file_path = "../data/bl_books/sample/book_data_sample.json"

### Printing

Print the entire document:

In [123]:
!jq "." {json_file_path}

[
  {
    "datefield": "1841",
    "shelfmarks": [
      "British Library HMNTS 11601.ddd.2."
    ],
    "publisher": "Privately printed",
    "title": [
      "The Poetical Aviary, with a bird's-eye view of the English poets. [The preface signed: A. A.] Ms. notes"
    ],
    "edition": "",
    "flickr_url_to_book_images": "http://www.flickr.com/photos/britishlibrary/tags/sysnum000000196",
    "place": "Calcutta",
    "issuance": "monographic",
    "authors": {
      "creator": [
        "A. A."
      ]
    },
    "date": "1841",
    "pdf": {
      "1": "lsidyv35c55757"
    },
    "identifier": "000000196",
    "corporate": {},
    "fulltext_filename": "sample/full_texts/000000196_01_text.json"
  },
  {
    "datefield": "1888",
    "imgs": {
      "0": {
        "000257": [
          "11104648374"
        ]
      }
    },
    "shelfmarks": [
      "British Library HMNTS 9025.cc.14."
    ],
    "publisher": "Rivingtons",
    "title": [
      "A History of Greece. Part I. From the earlie

        ],
        "000415": [
          "11057546644"
        ],
        "000418": [
          "11057310466"
        ],
        "000155": [
          "11057341125"
        ],
        "000624": [
          "11057670994"
        ],
        "000031": [
          "11057088415"
        ],
        "000621": [
          "11244672546"
        ],
        "000518": [
          "11244709124"
        ],
        "000315": [
          "11244964693"
        ],
        "000159": [
          "11056922226"
        ],
        "000092": [
          "11244156284"
        ],
        "000498": [
          "11244232625"
        ],
        "000393": [
          "11244852664"
        ],
        "000491": [
          "11244915123"
        ],
        "000255": [
          "11244373706"
        ],
        "000019": [
          "11057773476"
        ],
        "000398": [
          "11244191953"
        ],
        "000546": [
          "11244750326"
        ],
        "000429": [
          "11244685355"
        ],

    "edition": "",
    "flickr_url_to_book_images": "http://www.flickr.com/photos/britishlibrary/tags/sysnum000789156",
    "place": "London",
    "issuance": "monographic",
    "authors": {
      "creator": [
        "Cornwall, Barry"
      ]
    },
    "date": "1857",
    "pdf": {
      "1": "lsidyv36c49b8c"
    },
    "identifier": "000789156",
    "corporate": {},
    "fulltext_filename": "sample/full_texts/000789156_01_text.json"
  },
  {
    "datefield": "1886",
    "imgs": {
      "0": {
        "000067": [
          "11097579865"
        ]
      }
    },
    "shelfmarks": [
      "British Library HMNTS 11781.df.26."
    ],
    "publisher": "Warren Hall & Lovitt",
    "title": [
      "Jacques Artevelte ... [A play.] Edited by E. Ratcliffe Cousins"
    ],
    "edition": "",
    "flickr_url_to_book_images": "http://www.flickr.com/photos/britishlibrary/tags/sysnum000802657",
    "place": "London]",
    "issuance": "monographic",
    "authors": {
      "contributor": [
        "COU

        ],
        "000022": [
          "11127193143"
        ],
        "000120": [
          "11270460466"
        ],
        "000482": [
          "11122373866"
        ],
        "000223": [
          "11127610905"
        ],
        "000040": [
          "11124788205"
        ],
        "000031": [
          "11123470695"
        ],
        "000028": [
          "11126674446"
        ],
        "000182": [
          "11269102164"
        ],
        "000193": [
          "11268424305"
        ],
        "000459": [
          "11125920515"
        ],
        "000423": [
          "11268465765"
        ],
        "000163": [
          "11123135836"
        ],
        "000623": [
          "11073869915"
        ]
      }
    },
    "shelfmarks": [
      "British Library HMNTS 10408.bb.41.",
      "British Library DSC MFE/33/21019 *1*"
    ],
    "publisher": "App. ci. Payot, Upham & Co.",
    "title": [
      "The Hand-book to Arizona: its resources, history ... and scenery. ... Illu

    "publisher": "M. H. Gill & Son",
    "title": [
      "Poems"
    ],
    "edition": "",
    "flickr_url_to_book_images": "http://www.flickr.com/photos/britishlibrary/tags/sysnum002304750",
    "place": "Dublin",
    "issuance": "monographic",
    "authors": {
      "creator": [
        "MACCARTHY, Denis Florence."
      ]
    },
    "date": "1882",
    "pdf": {
      "1": "lsidyv35e195df"
    },
    "identifier": "002304750",
    "corporate": {},
    "fulltext_filename": "sample/full_texts/002304750_01_text.json"
  },
  {
    "datefield": "1851",
    "imgs": {
      "0": {
        "000010": [
          "11036094765"
        ],
        "000008": [
          "11036622886"
        ]
      }
    },
    "shelfmarks": [
      "British Library HMNTS 10106.e.21."
    ],
    "publisher": "",
    "title": [
      "The Escape, or, Loiterings amid the Scenes of Story and Song"
    ],
    "edition": "",
    "flickr_url_to_book_images": "http://www.flickr.com/photos/britishlibrary/tags/sysnum002

          "11007494063",
          "11007472033"
        ],
        "000174": [
          "11007150375",
          "11007127775"
        ],
        "000360": [
          "11007437024",
          "11007582323"
        ],
        "000364": [
          "11007223525",
          "11007391583"
        ],
        "000179": [
          "11007376946",
          "11007317043"
        ],
        "000087": [
          "11007083305",
          "11007321615"
        ],
        "000081": [
          "11007185705",
          "11007249546"
        ],
        "000240": [
          "11221502154",
          "11007370756"
        ],
        "000244": [
          "11007435793",
          "11007383396"
        ],
        "000161": [
          "11007325213",
          "11007149055"
        ],
        "000163": [
          "11007274866",
          "11007580593"
        ],
        "000166": [
          "11007088635",
          "11007311383"
        ]
      }
    },
    "shelfmarks": [
      "British Library HMN

However, especially with large JSON files, we don't want to print the entire document, but just to see what's inside.

Let's print the first document in the file:

In [124]:
!jq ".[0]" {json_file_path}

{
  "datefield": "1841",
  "shelfmarks": [
    "British Library HMNTS 11601.ddd.2."
  ],
  "publisher": "Privately printed",
  "title": [
    "The Poetical Aviary, with a bird's-eye view of the English poets. [The preface signed: A. A.] Ms. notes"
  ],
  "edition": "",
  "flickr_url_to_book_images": "http://www.flickr.com/photos/britishlibrary/tags/sysnum000000196",
  "place": "Calcutta",
  "issuance": "monographic",
  "authors": {
    "creator": [
      "A. A."
    ]

  "date": "1841",
  "pdf": {
    "1": "lsidyv35c55757"
  },
  "identifier": "000000196",
  "corporate": {},
  "fulltext_filename": "sample/full_texts/000000196_01_text.json"
}


Or the last document: 

In [121]:
!jq -c ".[-1]" {json_file_path}

{"datefield":"1884","shelfmarks":["British Library HMNTS 11779.bb.6"],"publisher":"","title":["Cosmo de' Medici. The false one. Agramont and Beaumont. Three tragedies. And The deformed. A dramatic sketch. By the author of “Ginevra”"],"edition":"","flickr_url_to_book_images":"http://www.flickr.com/photos/britishlibrary/tags/sysnum004088699","place":"enk","issuance":"monographic","authors":{"creator":["Nutt, D. - Miss"]},"date":"1884","pdf":{"1":"lsidyv3a9e61ac"},"identifier":"004088699","corporate":{},"fulltext_filename":"sample/full_texts/004088699_01_text.json"}


The `-c` flag makes `jq` print a more compact output.

What are the top-level keys of each document?

In [50]:
!jq -c ".[0]|keys" {json_file_path}

["authors","corporate","date","datefield","edition","flickr_url_to_book_images","fulltext_filename","identifier","issuance","pdf","place","publisher","shelfmarks","title"]


What did we do here?:
- with `.[0]` we selected the first document
- with `|` with passed on this document to a function
- with the `keys` function we get the keys (properties)

How many documents are there in this file?

In [126]:
!jq -c "[.[]]| length" {json_file_path}

452


To understand what `[.[]]` does in the line above, try to change it to `.[]` and run it again:

In [129]:
!jq -c ".[]| length" {json_file_path}

14
15
15
15
15
14
15
14
14
14
15
15
15
14
15
15
15
15
15
14
15
15
14
15
15
15
15
14
15
15
15
14
14
15
15
15
15
14
15
15
15
15
14
15
15
14
14
15
15
15
15
15
15
15
15
15
15
15
15
14
15
15
15
15
15
14
14
15
15
15
14
14
15
14
15
14
14
15
15
14
14
14
14
15
14
15
14
15
15
14
15
14
15
15
15
15
14
15
15
15
15
15
15
15
15
14
15
15
15
14
15
15
14
15
14
15
14
15
14
15
15
14
15
15
14
15
14
14
15
15
14
14
15
15
15
14
14
15
14
15
14
15
15
14
15
15
14
15
15
14
14
14
14
15
15
15
15
15
14
15
15
14
15
15
14
14
15
15
14
15
15
15
15
14
15
15
15
14
14
14
14
15
15
15
15
15
15
15
14
15
15
15
14
15
15
15
14
15
15
15
15
14
15
15
15
15
14
14
14
14
14
15
14
14
14
15
15
15
15
15
15
14
14
15
15
15
14
15
14
15
14
14
14
14
14
14
14
14
14
15
14
15
14
15
15
15
15
15
15
15
15
15
15
14
15
15
15
15
14
14
15
14
15
14
15
14
14
15
15
15
14
14
15
15
14
14
15
14
15
14
15
15
14
15
14
15
14
15
15
15
15
15
15
15
15
15
14
14
14
15
15
15
15
14
14
14
15
15
15
15
15
14
14
15
15
14
15
14
14
14
15
15
15
14
15
14
15
15
15
15
15
15
14
1

**Q**: Can you explain now what `[.[]]` does as opposed to `.[]` ?

### Counting

In [95]:
!jq -c "[.[] | .identifier ]| length" {json_file_path}

452


In [134]:
!jq -c "[.[] | .publisher] | unique | length" {json_file_path}

251


### Selecting

Let's say we want to know the earliest and oldest published book in our sample. We can work a bit with the `.date` field of each document.

In [139]:
!jq -c ".[]|.date" {json_file_path}

"1841"
"1888"
"1847"
"1892"
"1863"
"1899"
"1882"
"1828"
"1833"
"1864"
"1873"
"1867"
"1899"
"1893"
"1894"
"1876"
"1887"
"1896"
"1866"
"1885"
"1801"
"1878"
"1776"
"1874"
"1852"
"1860"
"1890"
"1837"
"1863"
"1802"
"1855"
"1794"
"1794"
"1841"
"1887"
"1843"
"1812"
"1849"
"1822"
"1869"
"1845"
"1863"
"1868"
"1869"
"1876"
"1888"
"1816"
"1896"
"1897"
"1810"
"1820"
"1802"
"1881"
"1868"
"1895"
"1818"
"1891"
"1888"
"1879"
"1888"
"1899"
"1898"
"1859"
"1896"
"1883"
"1884"
"1890"
"1848"
"1894"
"1889"
"1821"
"1836"
"1880"
"1823"
"1887"
"1770"
"1831"
"1896"
"1899"
"1897"
"1869"
"1826"
"1898"
"1884"
"1892"
"1856"
"1832"
"1897"
"1886"
"1868"
"1853"
"1861"
"1888"
"1892"
"1829"
"1822"
"1885"
"1879"
"1885"
""
"1822"
"1892"
"1731"
"1842"
"1882"
"1802"
"1885"
"1857"
"1886"
"1819"
"1830"
"1808"
"1822"
"1854"
"1778"
"1794"
"1817"
"1678"
"1825"
"1877"
"1821"
"1804"
"1877"
"1882"
"1894"
"1813"
"1864"
"1879"
"1805"
"1896"
"1875"
"1775"
"1885"
"1822"
"1683"
"1687"
"1775"
"1885"
"1841"
"1894"
"1760"
"1841"
"1874"
"18

In [137]:
!jq -c "min_by(.date)|.date" {json_file_path}

""


In [136]:
!jq -c "max_by(.date)|.date" {json_file_path}

"1899"


**Q**: what's the problem here?

In [145]:
# first, we remove empty publication dates
!jq -c "[.[]|.date | select(. != \"\")]" {json_file_path}

["1841","1888","1847","1892","1863","1899","1882","1828","1833","1864","1873","1867","1899","1893","1894","1876","1887","1896","1866","1885","1801","1878","1776","1874","1852","1860","1890","1837","1863","1802","1855","1794","1794","1841","1887","1843","1812","1849","1822","1869","1845","1863","1868","1869","1876","1888","1816","1896","1897","1810","1820","1802","1881","1868","1895","1818","1891","1888","1879","1888","1899","1898","1859","1896","1883","1884","1890","1848","1894","1889","1821","1836","1880","1823","1887","1770","1831","1896","1899","1897","1869","1826","1898","1884","1892","1856","1832","1897","1886","1868","1853","1861","1888","1892","1829","1822","1885","1879","1885","1822","1892","1731","1842","1882","1802","1885","1857","1886","1819","1830","1808","1822","1854","1778","1794","1817","1678","1825","1877","1821","1804","1877","1882","1894","1813","1864","1879","1805","1896","1875","1775","1885","1822","1683","1687","1775","1885","1841","1894","1760","1841","1874","1873

In [147]:
# second, we convert the string value to a number
!jq -c "[.[]|.date | select(. != \"\") | tonumber]" {json_file_path}

[1841,1888,1847,1892,1863,1899,1882,1828,1833,1864,1873,1867,1899,1893,1894,1876,1887,1896,1866,1885,1801,1878,1776,1874,1852,1860,1890,1837,1863,1802,1855,1794,1794,1841,1887,1843,1812,1849,1822,1869,1845,1863,1868,1869,1876,1888,1816,1896,1897,1810,1820,1802,1881,1868,1895,1818,1891,1888,1879,1888,1899,1898,1859,1896,1883,1884,1890,1848,1894,1889,1821,1836,1880,1823,1887,1770,1831,1896,1899,1897,1869,1826,1898,1884,1892,1856,1832,1897,1886,1868,1853,1861,1888,1892,1829,1822,1885,1879,1885,1822,1892,1731,1842,1882,1802,1885,1857,1886,1819,1830,1808,1822,1854,1778,1794,1817,1678,1825,1877,1821,1804,1877,1882,1894,1813,1864,1879,1805,1896,1875,1775,1885,1822,1683,1687,1775,1885,1841,1894,1760,1841,1874,1873,1851,1884,1876,1879,1848,1895,1890,1874,1827,1892,1892,1846,1877,1889,1833,1891,1757,1776,1869,1820,1882,1826,1888,1872,1875,1836,1815,1892,1818,1849,1857,1866,1880,1671,1895,1897,1895,1826,1828,1876,1812,1893,1833,1823,1874,1873,1896,1794,1881,1878,1895,1794,1858,1775,1889,1864,1882

In [148]:
!jq -c "[.[]|.date | select(. != \"\") | tonumber] | min" {json_file_path}

1663


In [112]:
!jq -c "[.[]|.date | select(. != \"\") | tonumber] | max" {json_file_path}

1899


## CSV

### `csvkit`

Overview main commands in `csvkit`:

| Command       | Function           |
| ------------- |-------------------- | 
| `csvlook`     | Pretty print of content (like `cat`) | 
| `csvgrep`     | Filter by text/regexp search (like `grep`) |
| `csvcut`      | Select, reorder columns |
| `csvsort`     | Sorting of rows by a given column


Pipes `|` for the win! All these commands can be piped into one another (and into virtually any bash command) to do wonders with a single line.

In [61]:
# TODO: do the same but using another example file, this is not ideal
# to showcase the functionalities of CSVKIT
csv_file_path = "../data/musk_tweets/elonmusk_tweets.csv"

In [4]:
!csvcut -n {csv_file_path}

  1: id
  2: created_at
  3: text


In [19]:
!csvcut -c id,created_at {csv_file_path} | csvjson

[{"id": 8.496368680522752e+17, "created_at": "2017-04-05T14:56:29"}, {"id": 8.489887305850962e+17, "created_at": "2017-04-03T20:01:01"}, {"id": 8.489430724234977e+17, "created_at": "2017-04-03T16:59:35"}, {"id": 8.4893570505728e+17, "created_at": "2017-04-03T16:30:19"}, {"id": 8.484160495736586e+17, "created_at": "2017-04-02T06:05:23"}, {"id": 8.484157315029238e+17, "created_at": "2017-04-02T06:04:07"}, {"id": 8.484153562637025e+17, "created_at": "2017-04-02T06:02:38"}, {"id": 8.48398971139629e+17, "created_at": "2017-04-02T04:57:31"}, {"id": 8.482445775216476e+17, "created_at": "2017-04-01T18:44:01"}, {"id": 8.482433509938954e+17, "created_at": "2017-04-01T18:39:09"}, {"id": 8.482399280434913e+17, "created_at": "2017-04-01T18:25:33"}, {"id": 8.482396645362237e+17, "created_at": "2017-04-01T18:24:30"}, {"id": 8.480360432406364e+17, "created_at": "2017-04-01T04:55:23"}, {"id": 8.479585718956196e+17, "created_at": "2017-03-31T23:47:32"}, {"id": 8.47890916048339e+17, "created_at": "2017-0

85504e+17, "created_at": "2013-05-03T18:24:48"}, {"id": 3.3036497530035814e+17, "created_at": "2013-05-03T16:55:22"}, {"id": 3.302411156703273e+17, "created_at": "2013-05-03T08:43:12"}, {"id": 3.3024066548309606e+17, "created_at": "2013-05-03T08:41:24"}, {"id": 3.3005400214851584e+17, "created_at": "2013-05-02T20:19:40"}, {"id": 3.300534502619873e+17, "created_at": "2013-05-02T20:17:29"}, {"id": 3.300192802068316e+17, "created_at": "2013-05-02T18:01:42"}, {"id": 3.300175521200333e+17, "created_at": "2013-05-02T17:54:50"}, {"id": 3.297652005909299e+17, "created_at": "2013-05-02T01:12:05"}, {"id": 3.2976420471638016e+17, "created_at": "2013-05-02T01:08:07"}, {"id": 3.29652668547072e+17, "created_at": "2013-05-01T17:44:55"}, {"id": 3.296422403538944e+17, "created_at": "2013-05-01T17:03:29"}, {"id": 3.2963532182430925e+17, "created_at": "2013-05-01T16:35:59"}, {"id": 3.2963452374471885e+17, "created_at": "2013-05-01T16:32:49"}, {"id": 3.296339108981678e+17, "created_at": "2013-05-01T16:30:

In [27]:
!csvlook {csv_file_path} | less -S

|                      id |          created_at | text                          
| ----------------------- | ------------------- | ------------------------------
| 849,636,868,052,275,200 | 2017-04-05 14:56:29 | b'And so the robots spared hum
| 848,988,730,585,096,192 | 2017-04-03 20:01:01 | b"@ForIn2020 @waltmossberg @mi
| 848,943,072,423,497,728 | 2017-04-03 16:59:35 | b'@waltmossberg @mims @defcon_
| 848,935,705,057,280,001 | 2017-04-03 16:30:19 | b'Stormy weather in Shortville
| 848,416,049,573,658,624 | 2017-04-02 06:05:23 | b"@DaveLeeBBC @verge Coal is d
| 848,415,731,502,923,777 | 2017-04-02 06:04:07 | b"@Lexxxzis It's just a helico
| 848,415,356,263,702,528 | 2017-04-02 06:02:38 | b"@verge It won't matter"     
| 848,398,971,139,629,057 | 2017-04-02 04:57:31 | b'@SuperCoolCube Pretty good' 
| 848,244,577,521,647,616 | 2017-04-01 18:44:01 | b"Why did we waste so much tim
| 848,243,350,993,895,424 | 2017-04-01 18:39:09 | b'Technology breakthrough: tur
| 848,239,928,043,491,328 | 

In [10]:
!csvstat {csv_file_path}

  1. "id"

	Type of data:          Number
	Contains null values:  False
	Unique values:         2819
	Smallest value:        15,434,727,182
	Largest value:         849,636,868,052,275,200
	Sum:                   1,636,386,616,202,731,779,082
	Mean:                  580,484,787,585,218,793.573
	Median:                656,971,866,163,277,825
	StDev:                 218,640,394,647,883,942.006
	Most common values:    849,636,868,052,275,200 (1x)
	                       848,988,730,585,096,192 (1x)
	                       848,943,072,423,497,728 (1x)
	                       848,935,705,057,280,001 (1x)
	                       848,416,049,573,658,624 (1x)

  2. "created_at"

	Type of data:          DateTime
	Contains null values:  False
	Unique values:         2819
	Smallest value:        2010-06-04 18:31:57
	Largest value:         2017-04-05 14:56:29
	Most common values:    2017-04-05 14:56:29 (1x)
	                       2017-04-03 20:01:01 (1x)
	                       2017-04-03 16:59:35

In [47]:
!csvgrep -c created_at -m 2017-04 {csv_file_path} | csvcut -c id,created_at

id,created_at
849636868052275200,2017-04-05 14:56:29
848988730585096192,2017-04-03 20:01:01
848943072423497728,2017-04-03 16:59:35
848935705057280001,2017-04-03 16:30:19
848416049573658624,2017-04-02 06:05:23
848415731502923777,2017-04-02 06:04:07
848415356263702528,2017-04-02 06:02:38
848398971139629057,2017-04-02 04:57:31
848244577521647616,2017-04-01 18:44:01
848243350993895424,2017-04-01 18:39:09
848239928043491328,2017-04-01 18:25:33
848239664536223745,2017-04-01 18:24:30
848036043240636417,2017-04-01 04:55:23


In [60]:
!csvgrep -c text -m RT {csv_file_path} | csvcut -c id,created_at |csvsort -c created_at -r

id,created_at
848239928043491328,2017-04-01T18:25:33
848239664536223745,2017-04-01T18:24:30
847610880506208257,2017-03-31T00:45:56
847580067446345728,2017-03-30T22:43:30
847561780532523008,2017-03-30T21:30:50
847510437054877698,2017-03-30T18:06:48
845447146111303681,2017-03-25T01:28:01
845294849049870337,2017-03-24T15:22:51
845294411072204801,2017-03-24T15:21:07
845292886623109120,2017-03-24T15:15:03
845291692206960641,2017-03-24T15:10:18
845291064583892992,2017-03-24T15:07:49
845289583575105536,2017-03-24T15:01:56
845288100754444288,2017-03-24T14:56:02
845286473905553408,2017-03-24T14:49:34
845285144436998144,2017-03-24T14:44:17
844358371616567296,2017-03-22T01:21:37
843504884154417153,2017-03-19T16:50:10
842447592172675072,2017-03-16T18:48:52
842400698025172992,2017-03-16T15:42:32
842400673043898368,2017-03-16T15:42:26
842392886494683136,2017-03-16T15:11:29
838555180656295936,2017-03-06T01:01:49
833330869293035520,2017-02-19T15:02:16
833329764232372224,2017-02-19T14:57:52
83295405873

626979025190301696,2015-07-31T04:53:42
620358355240947712,2015-07-12T22:25:32
619579138181967872,2015-07-10T18:49:12
617719485768843265,2015-07-05T15:39:36
615114562766008320,2015-06-28T11:08:34
614258809473626112,2015-06-26T02:28:07
613121687698018304,2015-06-22T23:09:36
610479010309541888,2015-06-15T16:08:32
606942167072776192,2015-06-05T21:54:23
605878361613725696,2015-06-02T23:27:12
601501265332477952,2015-05-21T21:34:11
599964926992486401,2015-05-17T15:49:20
599391754786181122,2015-05-16T01:51:45
599391737094635520,2015-05-16T01:51:40
598174400404262912,2015-05-12T17:14:25
595960278610616320,2015-05-06T14:36:17
595477224481955840,2015-05-05T06:36:48
592481964419993601,2015-04-27T00:14:42
592471975869620225,2015-04-26T23:35:01
589505551366639618,2015-04-18T19:07:30
589082811119763458,2015-04-17T15:07:41
588145052981014531,2015-04-15T01:01:22
588059410137755649,2015-04-14T19:21:03
587682798644805633,2015-04-13T18:24:32
587681982546448384,2015-04-13T18:21:17
587488583591849984,2015-0

In [62]:
!csvgrep -c text -m RT {csv_file_path} | csvcut -c id,created_at |csvsort -c created_at -r | csvjson

[{"id": 8.482399280434913e+17, "created_at": "2017-04-01T18:25:33"}, {"id": 8.482396645362237e+17, "created_at": "2017-04-01T18:24:30"}, {"id": 8.476108805062083e+17, "created_at": "2017-03-31T00:45:56"}, {"id": 8.475800674463457e+17, "created_at": "2017-03-30T22:43:30"}, {"id": 8.47561780532523e+17, "created_at": "2017-03-30T21:30:50"}, {"id": 8.475104370548777e+17, "created_at": "2017-03-30T18:06:48"}, {"id": 8.454471461113037e+17, "created_at": "2017-03-25T01:28:01"}, {"id": 8.452948490498703e+17, "created_at": "2017-03-24T15:22:51"}, {"id": 8.452944110722048e+17, "created_at": "2017-03-24T15:21:07"}, {"id": 8.452928866231091e+17, "created_at": "2017-03-24T15:15:03"}, {"id": 8.452916922069606e+17, "created_at": "2017-03-24T15:10:18"}, {"id": 8.45291064583893e+17, "created_at": "2017-03-24T15:07:49"}, {"id": 8.452895835751055e+17, "created_at": "2017-03-24T15:01:56"}, {"id": 8.452881007544443e+17, "created_at": "2017-03-24T14:56:02"}, {"id": 8.452864739055534e+17, "created_at": "2017